In [6]:
import re
import string
import graphlab as gl # this import will be assumed from now on
import pandas as pd
import funcy as fp
import pyLDAvis
import pyLDAvis.graphlab

gl.set_runtime_config('GRAPHLAB_DEFAULT_NUM_PYLAMBDA_WORKERS', 24)
pyLDAvis.enable_notebook()

In [7]:
stories_sf = gl.load_sframe("hacker_news_stories.sframe") #gl.load_sframe("http://s3.amazonaws.com/dato-datasets/hacker_news/stories_with_text.sframe")

In [10]:
re_print = re.compile(r'[^' + string.printable + ']')
re_contraction = re.compile(r'(\w+)\s+(t|ve|d|ll|m|re)\b')

def combine_and_clean(row):
    cat = row["title"] + ' ' + row["text"]
    ascii = re_print.sub(' ', cat)
    fixed = re_contraction.sub(lambda m: "'".join(m.groups()), ascii)
    return fixed

stories_sf["text_title"] = stories_sf.apply(combine_and_clean)

In [11]:
stories_sf.save("hn_cleaned.sframe")

In [12]:
sample = stories_sf # U# stories_sf.sample(0.4, seed=42)
del sample["text"]
del sample["title"]

In [13]:
df = sample.to_dataframe()

In [14]:
from joblib import Parallel, delayed, cpu_count

def _series_chunks(s, n_jobs):
    if n_jobs < 0:
        # so, have n chunks if we are using all n cores/cpus = cpu_count() + 1 + n_jobs
        n_jobs = cpu_count() + 1 + n_jobs
    n = len(s)
    n_chunks = int(n / n_jobs)
    return (s.iloc[ilocs] for ilocs in fp.chunks(n_chunks, range(n)))

def series_pmap(s, f, n_jobs=-1):
    if n_jobs == 0:
        return s.map(f)
    return pd.concat(Parallel(n_jobs=n_jobs)(delayed(series_pmap)(sub_series, f, n_jobs=0) \
                                                 for sub_series in _series_chunks(s, n_jobs)))

In [15]:
from spacy.en import English
nlp = English()

In [16]:
def tokenize(s):
    tokens = nlp(unicode(s))
    # graphlab doesn't handle namedtuples (or even tuples) so we have to use a list :(
    return [[t.orth_.lower(), t.lemma_.lower(), t.pos, t.tag] for t in tokens if t.orth_.strip()]

In [17]:
def tokenize_d(s):
    tokens = nlp(unicode(s))
    # graphlab doesn't handle namedtuples (or even tuples) so we have to use a list :(
    return [[t.orth_, t.lemma_.lower(), t.pos_, t.tag_] for t in tokens if t.orth_.strip()]

In [18]:
%%time
tokens = series_pmap(df['text_title'], tokenize)

CPU times: user 3min 21s, sys: 39.6 s, total: 4min 1s
Wall time: 25min 10s


In [19]:
stories_sf["tokens"] = gl.SArray(tokens)

In [20]:
stories_sf.save("hn_cleaned_n_tokenized.sframe")

In [21]:
import spacy.parts_of_speech as pos

DEFAULT_POS = set([pos.NOUN, pos.VERB, pos.ADV, pos.ADJ])
DEFAULT_STOPWORDS = gl.text_analytics.stopwords() | set(['pm','am', "'re", "'ve", "n't", 'thing'])

In [22]:
# chunks to train Phrases with
def chunk(tokens, allowed_pos=DEFAULT_POS):
    split = []
    for token in tokens:
        orth, lemma, pos, tag = token
        if pos in allowed_pos:
            split.append(lemma)
        else:
            # break detected!
            if len(split) > 1:
                yield split
            if len(split) > 0:
                split = []
        

In [23]:
%%time
def chunk_doc(tokens):
    return list(chunk(tokens))
    
chunked_docs = tokens.map(chunk_doc)

CPU times: user 28.5 s, sys: 2.19 s, total: 30.7 s
Wall time: 30.4 s


In [24]:
contiguous_chunks = fp.cat(chunked_docs)

In [25]:
from gensim.models.phrases import Phrases

[INFO] Could not import Theano, will use standard float for default ShardedCorpus dtype.
/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/numpy/lib/utils.py:95: DeprecationWarning: `scipy.sparse.sparsetools` is deprecated!
scipy.sparse.sparsetools is a private module for scipy.sparse, and should not be used.
  warnings.warn(depdoc, DeprecationWarning)
/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/scipy/lib/_util.py:67: DeprecationWarning: Module scipy.linalg.blas.fblas is deprecated, use scipy.linalg.blas instead
  DeprecationWarning)
/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/scipy/lib/_util.py:67: DeprecationWarning: Module scipy.linalg.blas.fblas is deprecated, use scipy.linalg.blas instead
  DeprecationWarning)
/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/scipy/lib/_util.py:67: DeprecationWarning: Module scipy.linalg.blas.fblas is depr

In [26]:
%%time
# train chunker now
bigram = Phrases(contiguous_chunks)
trigram = Phrases(bigram[contiguous_chunks])


[INFO] collecting all words and their counts
[INFO] PROGRESS: at sentence #0, processed 0 words and 0 word types
[INFO] PROGRESS: at sentence #10000, processed 17397 words and 18410 word types
[INFO] PROGRESS: at sentence #20000, processed 34388 words and 32442 word types
[INFO] PROGRESS: at sentence #30000, processed 52011 words and 45045 word types
[INFO] PROGRESS: at sentence #40000, processed 69618 words and 57212 word types
[INFO] PROGRESS: at sentence #50000, processed 87074 words and 68103 word types
[INFO] PROGRESS: at sentence #60000, processed 104624 words and 78584 word types
[INFO] PROGRESS: at sentence #70000, processed 122055 words and 89103 word types
[INFO] PROGRESS: at sentence #80000, processed 139804 words and 100264 word types
[INFO] PROGRESS: at sentence #90000, processed 157386 words and 109643 word types
[INFO] PROGRESS: at sentence #100000, processed 174403 words and 119006 word types
[INFO] PROGRESS: at sentence #110000, processed 191929 words and 128681 word t

CPU times: user 5min 49s, sys: 26.6 s, total: 6min 16s
Wall time: 5min 59s


In [27]:
%%time
tokenized_and_filtered_docs = chunked_docs.map(fp.cat)

CPU times: user 5.08 s, sys: 984 ms, total: 6.06 s
Wall time: 5.62 s


In [28]:
def extract_chunks(doc, min_len=3):
    return [w for w in trigram[bigram[doc]] if len(w) >= min_len and w not in DEFAULT_STOPWORDS]

In [29]:
%%time
processed_docs = series_pmap(tokenized_and_filtered_docs, extract_chunks)

CPU times: user 1min 8s, sys: 27.2 s, total: 1min 35s
Wall time: 1min 59s


In [35]:
stories_sf["processed"] = gl.SArray(processed_docs)
stories_sf.save("hn_processed.sframe")

In [10]:
stories_sf = gl.load_sframe("hn_processed.sframe")

In [11]:
from gensim.corpora import Dictionary, MmCorpus


[INFO] Could not import Theano, will use standard float for default ShardedCorpus dtype.
/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/numpy/lib/utils.py:95: DeprecationWarning: `scipy.sparse.sparsetools` is deprecated!
scipy.sparse.sparsetools is a private module for scipy.sparse, and should not be used.
  warnings.warn(depdoc, DeprecationWarning)
/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/scipy/lib/_util.py:67: DeprecationWarning: Module scipy.linalg.blas.fblas is deprecated, use scipy.linalg.blas instead
  DeprecationWarning)
/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/scipy/lib/_util.py:67: DeprecationWarning: Module scipy.linalg.blas.fblas is deprecated, use scipy.linalg.blas instead
  DeprecationWarning)
/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/scipy/lib/_util.py:67: DeprecationWarning: Module scipy.linalg.blas.fblas is depr

In [13]:
%%time
dictionary = Dictionary(stories_sf["processed"])

[INFO] adding document #0 to Dictionary(0 unique tokens: [])
[INFO] adding document #10000 to Dictionary(63652 unique tokens: [u'fawn', u'faecal_transplant', u'name&#x27;s', u'joi_ito', u'machine&#x27;s']...)
[INFO] adding document #20000 to Dictionary(83250 unique tokens: [u'fawn', u'sucess', u'faecal_transplant', u'name&#x27;s', u'joi_ito']...)
[INFO] adding document #30000 to Dictionary(110342 unique tokens: [u'fawn', u'verplank', u'joi_ito', u'machine&#x27;s', u'relevant)<p']...)
[INFO] adding document #40000 to Dictionary(191538 unique tokens: [u'verplank', u'hands.<p>i&#x27;m', u'mainly_consist', u'sowell', u'polling/voting']...)
[INFO] adding document #50000 to Dictionary(228457 unique tokens: [u'm_context', u'verplank', u'hands.<p>i&#x27;m', u'piston_console', u'mainly_consist']...)
[INFO] adding document #60000 to Dictionary(241406 unique tokens: [u'm_context', u'verplank', u'hands.<p>i&#x27;m', u'piston_console', u'mainly_consist']...)
[INFO] adding document #70000 to Diction

CPU times: user 1min 27s, sys: 2.06 s, total: 1min 29s
Wall time: 1min 39s


In [32]:
dictionary.save('unfiltered.dict')

[INFO] saving Dictionary object under unfiltered.dict, separately None


In [14]:
dictionary.filter_extremes(no_below=5, no_above=0.3, keep_n=None)
dictionary.compactify()

[INFO] discarding 503561 tokens: [(u'mr._costolo', 2), (u'gaillard/reuters', 1), (u'london_taxi', 4), (u'ltda', 3), (u'confusables', 1), (u'confusable', 4), (u'utr', 1), (u'chgrp', 4), (u'runhost', 1), (u'filemap', 1)]...
[INFO] keeping 115998 tokens which were in no less than 5 and no more than 76191 (=30.0%) documents
[INFO] resulting dictionary: Dictionary(115998 unique tokens: [u'fawn', u'unsupportable', u'joi_ito', u'mainly_consist', u'sonja']...)


In [19]:
def doc2bags(dictionary, doc):    
    return {dictionary[id]: count for id, count in dictionary.doc2bow(doc)}    

In [22]:
%%time
bows = stories_sf["processed"].apply(fp.partial(doc2bags, dictionary))

CPU times: user 2.84 s, sys: 263 ms, total: 3.1 s
Wall time: 4.42 s


In [23]:
topic_model100 = gl.topic_model.create(bows, num_topics=100, num_iterations=200)

PROGRESS: Learning a topic model
PROGRESS:        Number of documents    253973
PROGRESS:            Vocabulary size    115998
PROGRESS:    Running collapsed Gibbs sampling
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | Iteration | Elapsed Time  | Tokens/Second  | Est. Perplexity |
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | 10        | 55.15s        | 2.49533e+06    | 0               |
PROGRESS: | 20        | 1m 42s        | 2.55197e+06    | 0               |
PROGRESS: | 30        | 2m 29s        | 2.42161e+06    | 0               |
PROGRESS: | 40        | 3m 17s        | 2.40682e+06    | 0               |
PROGRESS: | 50        | 4m 4s         | 2.51469e+06    | 0               |
PROGRESS: | 60        | 4m 51s        | 2.4741e+06     | 0               |
PROGRESS: | 70        | 5m 38s        | 2.47171e+06    | 0               |
PROGRESS: | 80        | 6m 26s        | 2.37051e+06    | 0               |
PR

In [24]:
%%time
vis_data100 = pyLDAvis.graphlab.prepare(topic_model100, bows)

CPU times: user 3min 31s, sys: 7.04 s, total: 3min 38s
Wall time: 5min 10s


/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/skbio/stats/ordination/_principal_coordinate_analysis.py:107: RuntimeWarning: The result contains negative eigenvalues. Please compare their magnitude with the magnitude of some of the largest positive eigenvalues. If the negative ones are smaller, it's probably safe to ignore them, but if they are large in magnitude, the results won't be useful. See the Notes section for more details. The smallest eigenvalue is -0.00591032736493 and the largest is 1.11497827866.
  RuntimeWarning


In [31]:
vis_data100

PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
30     2.287611        1       1 -0.129647  0.087757
64     2.124373        1       2  0.076708  0.224064
65     1.700713        1       3 -0.250556  0.014536
80     1.592263        1       4 -0.276779  0.153229
52     1.546258        1       5 -0.026924  0.187959
58     1.506463        1       6 -0.056366 -0.033566
66     1.468854        1       7  0.044781  0.174874
50     1.463340        1       8 -0.068105  0.094988
16     1.431524        1       9  0.056817  0.217159
8      1.363299        1      10  0.032897 -0.049823
20     1.335215        1      11 -0.062375 -0.100794
59     1.334178        1      12  0.009054  0.182536
4      1.325628        1      13 -0.124980 -0.039228
34     1.325544        1      14 -0.279085  0.041224
86     1.301157        1      15  0.098954  0.201502
97     1.293074        1      16  0.006779  0.062349
9      1.293069        1      17 -0.015041 -0.138671
60     1.247991        1      18 -0.222528  0.079632
5      1.245604        1      19 -0.025394  0.141610
21     1.239364        1      20  0.020085 -0.059100
51     1.213053        1      21  0.006286  0.037625
2      1.213023        1      22 -0.059664 -0.044228
38     1.189150        1      23  0.020197 -0.103193
11     1.174390        1      24 -0.033626  0.047271
1      1.154885        1      25  0.011257 -0.042451
92     1.145478        1      26 -0.246584  0.066875
78     1.132684        1      27  0.119358  0.143844
79     1.129903        1      28  0.126711  0.048257
18     1.127339        1      29 -0.009729  0.134387
12     1.124085        1      30  0.158152  0.134929
...         ...      ...     ...       ...       ...
44     0.827939        1      71  0.004522 -0.070077
76     0.826214        1      72  0.167912 -0.030870
41     0.819532        1      73  0.070453  0.004141
39     0.814739        1      74 -0.082952 -0.066112
99     0.814434        1      75  0.053414 -0.168076
26     0.800158        1      76 -0.176698  0.036315
54     0.791526        1      77  0.104137  0.006325
75     0.780097        1      78  0.038667 -0.108507
70     0.778727        1      79  0.043130 -0.004027
82     0.776135        1      80 -0.105793  0.084949
43     0.774417        1      81 -0.023453 -0.089740
28     0.770047        1      82 -0.227967  0.058388
62     0.763620        1      83 -0.144380 -0.031235
83     0.759532        1      84 -0.003962 -0.110961
77     0.750799        1      85  0.115143 -0.068920
84     0.728582        1      86 -0.024190 -0.024294
7      0.711803        1      87  0.080842 -0.052130
95     0.692092        1      88 -0.015305 -0.027885
0      0.663805        1      89  0.066281 -0.034360
81     0.656808        1      90 -0.042162  0.026561
42     0.646800        1      91  0.053403 -0.120865
68     0.613605        1      92  0.035097 -0.140021
37     0.592735        1      93 -0.056220 -0.029440
56     0.588261        1      94  0.148834 -0.134348
24     0.550999        1      95  0.067392 -0.160357
29     0.521188        1      96  0.039503 -0.098335
35     0.509775        1      97  0.086785 -0.154182
33     0.486488        1      98  0.064344 -0.144135
27     0.472603        1      99 -0.031002 -0.123785
93     0.414565        1     100  0.028870 -0.113190

[100 rows x 5 columns], topic_info=        Category           Freq                     Term   Total  loglift  \
14784    Default   42831.000000                   ask_hn   42831  30.0000   
111186   Default   43571.000000                   google   43571  29.0000   
93464    Default   55306.000000                     data   55306  28.0000   
91192    Default   94198.000000                   people   94198  27.0000   
1900     Default   72314.000000                  company   72314  26.0000   
47035    Default   96957.000000                     work   96957  25.0000   
27068    Default   40389.000000                   desig

In [26]:
topic_model75 = gl.topic_model.create(bows, num_topics=75, num_iterations=200)

PROGRESS: Learning a topic model
PROGRESS:        Number of documents    253973
PROGRESS:            Vocabulary size    115998
PROGRESS:    Running collapsed Gibbs sampling
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | Iteration | Elapsed Time  | Tokens/Second  | Est. Perplexity |
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | 10        | 45.43s        | 2.89845e+06    | 0               |
PROGRESS: | 20        | 1m 25s        | 2.78779e+06    | 0               |
PROGRESS: | 30        | 2m 5s         | 2.98204e+06    | 0               |
PROGRESS: | 40        | 2m 46s        | 2.91351e+06    | 0               |
PROGRESS: | 50        | 3m 27s        | 2.84212e+06    | 0               |
PROGRESS: | 60        | 4m 8s         | 2.87685e+06    | 0               |
PROGRESS: | 70        | 4m 49s        | 2.95537e+06    | 0               |
PROGRESS: | 80        | 5m 30s        | 2.72292e+06    | 0               |
PR

In [27]:
%%time
vis_data75 = pyLDAvis.graphlab.prepare(topic_model75, bows)

CPU times: user 2min 58s, sys: 6.12 s, total: 3min 4s
Wall time: 4min 20s


In [32]:
vis_data75

PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
66     2.422834        1       1  0.071812 -0.129958
64     2.259274        1       2 -0.103162 -0.204403
60     2.115144        1       3  0.154053  0.031207
28     2.052298        1       4  0.058636 -0.182065
52     1.994761        1       5  0.006648  0.086172
23     1.956870        1       6 -0.070203 -0.226255
43     1.901095        1       7  0.152462 -0.031857
50     1.873637        1       8  0.246645 -0.079020
42     1.867441        1       9  0.076125  0.046853
54     1.849482        1      10  0.271879 -0.058979
27     1.751327        1      11  0.200869 -0.099774
74     1.750452        1      12  0.014613  0.002248
73     1.688131        1      13  0.075188  0.087002
17     1.657115        1      14  0.034923 -0.021370
56     1.640423        1      15  0.015195 -0.161719
44     1.577586        1      16  0.008662  0.000370
26     1.558593        1      17  0.269697 -0.115034
48     1.534590        1      18  0.065139  0.133106
19     1.525035        1      19 -0.016145  0.068136
53     1.518868        1      20 -0.170219 -0.146664
34     1.517186        1      21 -0.060186 -0.107216
65     1.516550        1      22  0.018602 -0.184573
63     1.512829        1      23  0.054361  0.127544
0      1.493216        1      24 -0.060183 -0.110612
12     1.425072        1      25 -0.105728 -0.060732
38     1.424577        1      26 -0.153820 -0.155844
6      1.410291        1      27  0.076294  0.059024
32     1.395380        1      28 -0.050910  0.029332
21     1.392853        1      29  0.047803  0.060811
69     1.388321        1      30  0.065570  0.076740
...         ...      ...     ...       ...       ...
4      1.218425        1      46  0.216518 -0.087268
61     1.207034        1      47  0.057382  0.097898
67     1.190468        1      48 -0.002801 -0.019055
55     1.178911        1      49  0.023762  0.059008
30     1.169369        1      50 -0.125055 -0.026007
72     1.164986        1      51  0.101900 -0.038013
15     1.156104        1      52  0.063339  0.093820
39     1.151258        1      53 -0.004164  0.068164
9      1.143594        1      54  0.047872  0.055059
71     1.136876        1      55 -0.022821  0.154784
14     1.136788        1      56 -0.008676  0.034400
36     1.121394        1      57 -0.111028  0.061897
8      1.112280        1      58 -0.163349  0.045527
70     1.082262        1      59 -0.071529  0.112916
57     1.053476        1      60 -0.143809 -0.110440
25     1.012003        1      61 -0.048169 -0.005111
35     1.008488        1      62 -0.064470  0.086706
31     0.959532        1      63 -0.087922  0.092812
1      0.956576        1      64  0.020900 -0.000461
5      0.951535        1      65 -0.015350  0.025598
24     0.806341        1      66 -0.126933  0.143401
47     0.794417        1      67  0.077586  0.022563
3      0.773493        1      68 -0.044018  0.175012
46     0.736598        1      69 -0.029726  0.167249
49     0.722643        1      70 -0.014620  0.191158
2      0.709767        1      71  0.142926  0.081991
7      0.674477        1      72 -0.039608  0.145467
40     0.641636        1      73 -0.015931  0.114268
59     0.628936        1      74  0.048453  0.107058
13     0.626755        1      75 -0.055648  0.154839

[75 rows x 5 columns], topic_info=       Category           Freq             Term   Total  loglift  logprob
14784   Default   42831.000000           ask_hn   42831  30.0000  30.0000
111186  Default   43571.000000           google   43571  29.0000  29.0000
91192   Default   94198.000000           people   94198  28.0000  28.0000
1900    Default   72314.000000          company   72314  27.0000  27.0000
93464   Default   55306.000000             data   55306  26.0000  26.0000
47035   Default   96957.000000             work   96957  25.0000  25.0000
27068   Default   40389.000000           design   40389  24.0000  24.0000
929